# Convert TEI into TSV


In [2]:
from lxml import etree
from collections import defaultdict
import re
import os

In [16]:
inputpath = os.path.join('..', 'data', '1743_LeRobert', 'tei', 'TR5.tei')
NS = {"tei": "http://www.tei-c.org/ns/1.0"}

tree = etree.parse(inputpath)
root = tree.getroot()

# On démarre à la page logique 1
page_num = 13
pages = defaultdict(list)

def add(text):
    text = re.sub(r"\s+", " ", text)
    if text.strip():
        pages[page_num].append(text.strip())

# 🔹 Parcours UNIQUEMENT du <text> (teiHeader ignoré)
text_root = root.find(".//tei:text", namespaces=NS)

for elem in text_root.iter():

    # Texte AVANT les enfants
    if elem.text:
        add(elem.text)

    # Gestion des sauts de page
    if elem.tag == "{http://www.tei-c.org/ns/1.0}pb":
        n = elem.get("n")

        # Saut seulement si n impair
        if n and n.isdigit() and int(n) % 2 == 1:
            page_num += 1

        # Le texte après <pb/> va sur la page courante
        if elem.tail:
            add(elem.tail)

        continue

    # Texte APRÈS l'élément
    if elem.tail:
        add(elem.tail)

# Fusion finale
pages = {p: " ".join(t) for p, t in pages.items()}



In [17]:
pages

{13: "PÉ pour Pierre , Il y a en France une Abbaye nommée S. Pé de Generès, en Latin S. Petri de Generofo. Pierre Fournier, Procureur au Parlement, signoit P. Fournier, pour se distinguer de quelques-uns de ses confrères qui portoient aussi le nom de Fournier : c'est pourquoi on l'appeloit ordinairement Pé-Fournier. Tous les Procureurs qui ont des confrères de même nom qu'eux, se distinguent ainsi par la première lettre de leur nom de batême. Dans la comédie Italienne d'Arlequin Procureur, Arlequin, pour imiter ce vers, Et dont les Cicerons se font chez Pé-Fournier. se nommoit Pé-Arlequin. Brossette sur le vers 124. de la I. sat. de Boileau. PEAAGKIRKE , Prononcez Péguire, & Voyez Pégue. PÉAGE , f. m. Il s'est dit autrefois en général de toutes sortes d'impôts qui se payoient sur les machandises qu'on transportoit d'un lieu à un autre. Vectigal, tributum, portorium. Maintenant il se dit d'un droit qu'on prend sur les voitures des marchandises pour l'entretien des grands chemins. Divers

In [20]:
inputpath = os.path.join('..', 'data', '1743_LeRobert', 'tei_txt_per_page')

for page, content in pages.items():
    with open(f"{inputpath}/page_{page}.txt", "w", encoding="utf-8") as f:
        f.write(content)

In [14]:

from lxml import etree
import re
from pathlib import Path

TEI_NS = "http://www.tei-c.org/ns/1.0"
NS = {"tei": TEI_NS}
LB_MARK = "\u241E"  # marqueur temporaire rare

def div_to_text(div_elem) -> str:
    parts = []
    for elem in div_elem.iter():
        # texte avant enfants
        if elem.text:
            parts.append(elem.text)

        # <lb/> -> marqueur (pas de saut de ligne)
        if etree.QName(elem).localname == "lb":
            parts.append(LB_MARK)

        # texte après la balise
        if elem.tail:
            parts.append(elem.tail)

    return "".join(parts)

def tei_article_to_txt(xml_path: str, txt_path: str) -> None:
    tree = etree.parse(xml_path)
    root = tree.getroot()

    # On ignore teiHeader automatiquement car on ne prend que les div sous <text>
    divs = root.xpath(".//tei:text//tei:div", namespaces=NS)

    chunks = [div_to_text(d) for d in divs]
    raw = " ".join(chunks)  # <-- séparation garantie entre divs

    # 1) recoller les mots coupés : "ap-<lb/> pelle" => "appelle"
    raw = re.sub(r"-\s*" + re.escape(LB_MARK) + r"\s*", "", raw)

    # 2) les <lb/> restants deviennent un espace
    raw = re.sub(re.escape(LB_MARK) + r"\s*", " ", raw)

    # 3) normaliser les espaces
    text = re.sub(r"\s+", " ", raw).strip()

    with open(txt_path, "w", encoding="utf-8") as f:
        f.write(text)


def process_tei_folder(input_dir: str, output_dir: str) -> None:
    input_path = Path(input_dir)
    output_path = Path(output_dir)
    output_path.mkdir(parents=True, exist_ok=True)

    for xml_file in input_path.glob("*.xml"):
        txt_file = output_path / (xml_file.stem + ".txt")
        tei_article_to_txt(xml_file, txt_file)
        print(f"✔ {xml_file.name} → {txt_file.name}")





In [15]:

inputpath = '/Users/lmoncla/Nextcloud/Recherche/Stages/2025-2026/Projet Pro IDL Grenoble/data/DUFLT_1743_5/ocr_tesseract_tei_page/'
outputpath = '/Users/lmoncla/Nextcloud/Recherche/Stages/2025-2026/Projet Pro IDL Grenoble/data/DUFLT_1743_5/ocr_tesseract_txt_page/'


process_tei_folder(
    input_dir=inputpath,
    output_dir=outputpath
)

✔ 1913247_84.xml → 1913247_84.txt
✔ 1913247_910.xml → 1913247_910.txt
✔ 1913247_904.xml → 1913247_904.txt
✔ 1913247_90.xml → 1913247_90.txt
✔ 1913247_938.xml → 1913247_938.txt
✔ 1913247_47.xml → 1913247_47.txt
✔ 1913247_53.xml → 1913247_53.txt
✔ 1913247_737.xml → 1913247_737.txt
✔ 1913247_723.xml → 1913247_723.txt
✔ 1913247_290.xml → 1913247_290.txt
✔ 1913247_284.xml → 1913247_284.txt
✔ 1913247_509.xml → 1913247_509.txt
✔ 1913247_253.xml → 1913247_253.txt
✔ 1913247_535.xml → 1913247_535.txt
✔ 1913247_521.xml → 1913247_521.txt
✔ 1913247_247.xml → 1913247_247.txt
✔ 1913247_482.xml → 1913247_482.txt
✔ 1913247_496.xml → 1913247_496.txt
✔ 1913247_469.xml → 1913247_469.txt
✔ 1913247_1.xml → 1913247_1.txt
✔ 1913247_327.xml → 1913247_327.txt
✔ 1913247_441.xml → 1913247_441.txt
✔ 1913247_455.xml → 1913247_455.txt
✔ 1913247_333.xml → 1913247_333.txt
✔ 1913247_864.xml → 1913247_864.txt
✔ 1913247_870.xml → 1913247_870.txt
✔ 1913247_858.xml → 1913247_858.txt
✔ 1913247_680.xml → 1913247_680.txt
✔ 19